In [ ]:
# %pip install billboard.py

In [1]:
import billboard
import pandas as pd
import numpy as np
import datetime

In [ ]:
# %reset

In [ ]:
# The official Billboard API has fallen out of use, see: https://stackoverflow.com/questions/7835398/how-to-get-billboard-hot-100-chart-listing-via-billboard-api/9613219
# This script uses the billboard.py package as documented here: https://github.com/guoguo12/billboard-charts

# When do charts update each week?
# Almost all weekly charts update each Tuesday morning (while, during weeks with Monday holidays, charts update on Wednesdays).

In [2]:
# Create a list of dates from 2015-01-01 to present day by weekly intervals (since this chart updates weekly)
# We start in 2015 because we want to give some prior history to artists appearing in 2017 (when the Spotify Top 200 Chart begins), 
# otherwise their mean rank/frequency would be undefined.

date_list = []
date_start = datetime.datetime(2015, 1, 1)
d = datetime.timedelta(days = 7)

while date_start <= datetime.datetime(2020, 12, 12): # can change this to whatever today's date is
    date_list.append(date_start)
    date_start += d

In [ ]:
# Fetch the Top 100 Artist chart for every week from the start date to present
chart_list = []
for i in range(len(date_list)):
    chart = billboard.ChartData('artist-100', date = date_list[i].strftime('%Y-%m-%d'))
    chart_list.append(chart)
    print('Downloaded', date_list[i])
    # a 5-second rest between every other ~5 calls is automatically built into the billboard.ChartDate() function

In [5]:
artist_list = []
rank_list = []
peakpos_list = []
lastpos_list = []
isnew_list = []
date_list_ext = []

# Create a long (stacked) list of Top 100 Artist for every week
for i in range(len(chart_list)):
    for j in range(100):
        # Append the date (each date will be repeated as many times as there are artists)
        date_list_ext.append(date_list[i])
        # Append the artist's name and rank
        artist_list.append(chart_list[i][j].artist)
        rank_list.append(chart_list[i][j].rank)
        # Append the artist's last position and peak position as of that date
        peakpos_list.append(chart_list[i][j].peakPos)
        lastpos_list.append(chart_list[i][j].lastPos)
        isnew_list.append(chart_list[i][j].isNew)

In [6]:
# Convert list to long dataframe
df = pd.DataFrame(list(zip(date_list_ext, artist_list, rank_list, peakpos_list, lastpos_list, isnew_list)), 
                  columns =['Date', 'Artist', 'BB Pos', 'Peak BB Pos', 'Last BB Pos', 'New'])

In [7]:
df

Date           Artist  BB Pos  Peak BB Pos  Last BB Pos    New
0     2015-01-01     Taylor Swift       1            1            1  False
1     2015-01-01      Nicki Minaj       2            2           12  False
2     2015-01-01       Ed Sheeran       3            3            4  False
3     2015-01-01       Pentatonix       4            2            3  False
4     2015-01-01        Sam Smith       5            1            5  False
...          ...              ...     ...          ...          ...    ...
31095 2020-12-10           Lady A      96            6           94  False
31096 2020-12-10       Elton John      97           11           96  False
31097 2020-12-10     Gwen Stefani      98            4            0  False
31098 2020-12-10  Michael Jackson      99           20            0  False
31099 2020-12-10    Granger Smith     100           28            0  False

[31100 rows x 6 columns]

In [8]:
df.to_csv('2020.12.12 Billboard Top 100 Artist.csv')

In [ ]:
# Summarize the rank based on all available observations
# df2 = df.groupby(['Artist'])[['BB Pos']].agg(['mean', 'count', 'max', 'min']).reset_index()
# df2 = df2.sort_values(by=['Artist'])
# df2.head(25)

In [10]:
date_list2 = [i for i in date_list if i >= datetime.datetime(2017, 1, 1)]

# Create a list of every combination of date - artist
outlist = [ (i, j)
    for i in date_list2
    for j in df.Artist.unique() ]

In [11]:
mean_rank = []
freq = []

# This step will take a while -- it will create ~ 225,364 observations
# For each pair of date i - artist j, calculate the cumulative mean of an artist j's rank
# and how many times the artist j has appeared on the Top 100 chart prior to and including date i

for i in date_list2:
    for j in list(df.Artist.unique()):
        mean_rank.append(df[(df['Date'] <= i) & 
                            (df['Artist'] == j)]['BB Pos'].mean())
        freq.append(len(df[(df['Date'] <= i) & 
                           (df['Artist'] == j)]['BB Pos']))
        
        # Print percentage completed to track progress
        print(len(freq)/(len(date_list2)*len(list(df.Artist.unique()))))

2.3300246982618015e-06
4.660049396523603e-06
6.990074094785405e-06
9.320098793047206e-06
1.1650123491309008e-05
1.398014818957081e-05
1.6310172887832612e-05
1.8640197586094412e-05
2.0970222284356216e-05
2.3300246982618016e-05
2.5630271680879816e-05
2.796029637914162e-05
3.029032107740342e-05
3.2620345775665224e-05
3.4950370473927024e-05
3.7280395172188824e-05
3.9610419870450625e-05
4.194044456871243e-05
4.427046926697423e-05
4.660049396523603e-05
4.893051866349783e-05
5.126054336175963e-05
5.359056806002143e-05
5.592059275828324e-05
5.825061745654504e-05
6.058064215480684e-05
6.291066685306865e-05
6.524069155133045e-05
6.757071624959225e-05
6.990074094785405e-05
7.223076564611585e-05
7.456079034437765e-05
7.689081504263945e-05
7.922083974090125e-05
8.155086443916305e-05
8.388088913742486e-05
8.621091383568666e-05
8.854093853394846e-05
9.087096323221026e-05
9.320098793047206e-05
9.553101262873386e-05
9.786103732699566e-05
0.00010019106202525747
0.00010252108672351927
0.00010485111142178

0.0008993895335290554
0.0009017195582273172
0.000904049582925579
0.0009063796076238408
0.0009087096323221026
0.0009110396570203644
0.0009133696817186262
0.0009156997064168881
0.0009180297311151499
0.0009203597558134116
0.0009226897805116734
0.0009250198052099352
0.000927349829908197
0.0009296798546064588
0.0009320098793047206
0.0009343399040029825
0.0009366699287012443
0.0009389999533995061
0.0009413299780977678
0.0009436600027960296
0.0009459900274942914
0.0009483200521925532
0.000950650076890815
0.0009529801015890769
0.0009553101262873387
0.0009576401509856005
0.0009599701756838623
0.000962300200382124
0.0009646302250803858
0.0009669602497786476
0.0009692902744769094
0.0009716202991751713
0.0009739503238734331
0.0009762803485716949
0.0009786103732699566
0.0009809403979682185
0.0009832704226664802
0.0009856004473647421
0.0009879304720630038
0.0009902604967612658
0.0009925905214595275
0.0009949205461577892
0.000997250570856051
0.0009995805955543128
0.0010019106202525747
0.0010042406449

0.0018034391164546343
0.0018057691411528963
0.001808099165851158
0.00181042919054942
0.0018127592152476816
0.0018150892399459435
0.0018174192646442052
0.001819749289342467
0.0018220793140407289
0.0018244093387389906
0.0018267393634372525
0.0018290693881355142
0.0018313994128337761
0.0018337294375320378
0.0018360594622302997
0.0018383894869285614
0.0018407195116268231
0.001843049536325085
0.0018453795610233468
0.0018477095857216087
0.0018500396104198704
0.0018523696351181323
0.001854699659816394
0.001857029684514656
0.0018593597092129177
0.0018616897339111794
0.0018640197586094413
0.001866349783307703
0.001868679808005965
0.0018710098327042266
0.0018733398574024885
0.0018756698821007502
0.0018779999067990122
0.0018803299314972739
0.0018826599561955356
0.0018849899808937975
0.0018873200055920592
0.0018896500302903211
0.0018919800549885828
0.0018943100796868448
0.0018966401043851065
0.0018989701290833684
0.00190130015378163
0.0019036301784798918
0.0019059602031781537
0.0019082902278764154

0.0026981686005871663
0.002700498625285428
0.0027028286499836897
0.002705158674681952
0.0027074886993802135
0.0027098187240784753
0.002712148748776737
0.0027144787734749987
0.002716808798173261
0.0027191388228715225
0.002721468847569784
0.002723798872268046
0.002726128896966308
0.0027284589216645698
0.0027307889463628315
0.002733118971061093
0.002735448995759355
0.002737779020457617
0.0027401090451558787
0.0027424390698541404
0.002744769094552402
0.0027470991192506643
0.002749429143948926
0.0027517591686471877
0.0027540891933454494
0.002756419218043711
0.0027587492427419732
0.002761079267440235
0.0027634092921384966
0.0027657393168367583
0.00276806934153502
0.002770399366233282
0.002772729390931544
0.0027750594156298056
0.0027773894403280673
0.0027797194650263294
0.002782049489724591
0.002784379514422853
0.0027867095391211146
0.0027890395638193763
0.0027913695885176384
0.0027936996132159
0.002796029637914162
0.0027983596626124235
0.0028006896873106857
0.0028030197120089474
0.0028053497

0.0035882380353231746
0.0035905680600214363
0.003592898084719698
0.0035952281094179597
0.0035975581341162214
0.0035998881588144836
0.0036022181835127453
0.003604548208211007
0.0036068782329092687
0.003609208257607531
0.0036115382823057925
0.0036138683070040542
0.003616198331702316
0.0036185283564005776
0.00362085838109884
0.0036231884057971015
0.003625518430495363
0.003627848455193625
0.003630178479891887
0.0036325085045901487
0.0036348385292884105
0.003637168553986672
0.003639498578684934
0.003641828603383196
0.0036441586280814577
0.0036464886527797194
0.003648818677477981
0.0036511487021762433
0.003653478726874505
0.0036558087515727667
0.0036581387762710284
0.00366046880096929
0.0036627988256675522
0.003665128850365814
0.0036674588750640756
0.0036697888997623373
0.0036721189244605995
0.003674448949158861
0.003676778973857123
0.0036791089985553846
0.0036814390232536463
0.0036837690479519084
0.00368609907265017
0.003688429097348432
0.0036907591220466936
0.0036930891467449557
0.00369541

...

0.6579756745421501
0.6579780045668484
0.6579803345915467
0.6579826646162449
0.6579849946409432
0.6579873246656415
0.6579896546903398
0.657991984715038
0.6579943147397362
0.6579966447644345
0.6579989747891327
0.658001304813831
0.6580036348385293
0.6580059648632276
0.6580082948879258
0.6580106249126241
0.6580129549373224
0.6580152849620206
0.6580176149867188
0.6580199450114171
0.6580222750361154
0.6580246050608136
0.6580269350855119
0.6580292651102102
0.6580315951349084
0.6580339251596067
0.658036255184305
0.6580385852090033
0.6580409152337015
0.6580432452583997
0.658045575283098
0.6580479053077962
0.6580502353324945
0.6580525653571928
0.6580548953818911
0.6580572254065893
0.6580595554312876
0.6580618854559859
0.6580642154806841
0.6580665455053823
0.6580688755300806
0.6580712055547788
0.6580735355794771
0.6580758656041754
0.6580781956288737
0.6580805256535719
0.6580828556782702
0.6580851857029685
0.6580875157276667
0.658089845752365
0.6580921757770632
0.6580945058017615
0.658096835826459

0.6589962253599888
0.6589985553846871
0.6590008854093853
0.6590032154340836
0.6590055454587819
0.6590078754834802
0.6590102055081783
0.6590125355328766
0.6590148655575749
0.6590171955822731
0.6590195256069714
0.6590218556316697
0.659024185656368
0.6590265156810662
0.6590288457057645
0.6590311757304628
0.659033505755161
0.6590358357798592
0.6590381658045575
0.6590404958292558
0.659042825853954
0.6590451558786523
0.6590474859033506
0.6590498159280488
0.6590521459527471
0.6590544759774454
0.6590568060021437
0.6590591360268419
0.6590614660515401
0.6590637960762384
0.6590661261009366
0.6590684561256349
0.6590707861503332
0.6590731161750315
0.6590754461997297
0.659077776224428
0.6590801062491263
0.6590824362738245
0.6590847662985228
0.659087096323221
0.6590894263479193
0.6590917563726175
0.6590940863973158
0.6590964164220141
0.6590987464467123
0.6591010764714106
0.6591034064961089
0.6591057365208072
0.6591080665455054
0.6591103965702036
0.6591127265949019
0.6591150566196001
0.659117386644298

0.6600144461531292
0.6600167761778275
0.6600191062025258
0.660021436227224
0.6600237662519223
0.6600260962766206
0.6600284263013187
0.660030756326017
0.6600330863507153
0.6600354163754136
0.6600377464001118
0.6600400764248101
0.6600424064495084
0.6600447364742066
0.6600470664989049
0.6600493965236032
0.6600517265483015
0.6600540565729996
0.6600563865976979
0.6600587166223962
0.6600610466470944
0.6600633766717927
0.660065706696491
0.6600680367211893
0.6600703667458875
0.6600726967705858
0.6600750267952841
0.6600773568199823
0.6600796868446805
0.6600820168693788
0.660084346894077
0.6600866769187753
0.6600890069434736
0.6600913369681719
0.6600936669928701
0.6600959970175684
0.6600983270422667
0.6601006570669649
0.6601029870916632
0.6601053171163614
0.6601076471410597
0.6601099771657579
0.6601123071904562
0.6601146372151545
0.6601169672398527
0.660119297264551
0.6601216272892493
0.6601239573139476
0.6601262873386458
0.660128617363344
0.6601309473880423
0.6601332774127405
0.6601356074374388

0.6610419870450627
0.661044317069761
0.6610466470944591
0.6610489771191574
0.6610513071438557
0.661053637168554
0.6610559671932522
0.6610582972179505
0.6610606272426488
0.661062957267347
0.6610652872920453
0.6610676173167436
0.6610699473414419
0.66107227736614
0.6610746073908383
0.6610769374155366
0.6610792674402348
0.6610815974649331
0.6610839274896314
0.6610862575143297
0.6610885875390279
0.6610909175637262
0.6610932475884245
0.6610955776131227
0.661097907637821
0.6611002376625192
0.6611025676872175
0.6611048977119157
0.661107227736614
0.6611095577613123
0.6611118877860105
0.6611142178107088
0.6611165478354071
0.6611188778601054
0.6611212078848036
0.6611235379095018
0.6611258679342001
0.6611281979588983
0.6611305279835966
0.6611328580082949
0.6611351880329932
0.6611375180576914
0.6611398480823897
0.661142178107088
0.6611445081317862
0.6611468381564845
0.6611491681811827
0.6611514982058809
0.6611538282305792
0.6611561582552775
0.6611584882799758
0.661160818304674
0.6611631483293723
0.

0.6620835080851857
0.662085838109884
0.6620881681345823
0.6620904981592804
0.6620928281839787
0.662095158208677
0.6620974882333752
0.6620998182580735
0.6621021482827718
0.6621044783074701
0.6621068083321683
0.6621091383568666
0.6621114683815649
0.662113798406263
0.6621161284309613
0.6621184584556596
0.6621207884803579
0.6621231185050561
0.6621254485297544
0.6621277785544527
0.6621301085791509
0.6621324386038492
0.6621347686285475
0.6621370986532458
0.662139428677944
0.6621417587026422
0.6621440887273405
0.6621464187520387
0.662148748776737
0.6621510788014353
0.6621534088261336
0.6621557388508318
0.6621580688755301
0.6621603989002284
0.6621627289249266
0.6621650589496249
0.6621673889743231
0.6621697189990214
0.6621720490237196
0.6621743790484179
0.6621767090731162
0.6621790390978144
0.6621813691225127
0.662183699147211
0.6621860291719093
0.6621883591966075
0.6621906892213058
0.662193019246004
0.6621953492707022
0.6621976792954005
0.6622000093200988
0.6622023393447971
0.6622046693694953


In [12]:
# Create a dataframe of each artist's cumulative mean rank and frequency on each of the available date
df3 = pd.DataFrame(data = outlist, columns = ['Date', 'Artist'])
df3['Cumu_mean_rank'] = mean_rank
df3['Cumu_frequency'] = freq

In [13]:
df3

Date            Artist  Cumu_mean_rank  Cumu_frequency
0      2017-01-05      Taylor Swift       12.122642             106
1      2017-01-05       Nicki Minaj       41.093750              96
2      2017-01-05        Ed Sheeran       30.620000             100
3      2017-01-05        Pentatonix       19.923077              26
4      2017-01-05         Sam Smith       30.411765              68
...           ...               ...             ...             ...
284275 2020-12-10          King Von       42.500000               4
284276 2020-12-10  System Of A Down       94.000000               1
284277 2020-12-10        Aesop Rock       88.000000               1
284278 2020-12-10              KISS       89.000000               1
284279 2020-12-10        Trey Lewis       52.000000               1

[284280 rows x 4 columns]

In [14]:
df3.to_csv('2020.12.12 Billboard Cumu Rank.csv')